### Precipitation - radar/gauge 5 minute real-time accumulations over the Netherlands 

The archive of gridded files of radar-derived 5 minute precipitation accumulations is corrected by rain gauge data. Radar data from 1500 m over the Netherlands and surrounding area measured by Dutch, Belgian, and German radars are corrected by available data from automatic rain gauges. Time interval is 5 minutes.

Starting with data from 31 January 2023 - 10.45 UTC onwards, this dataset is created using improved algorithms. This includes correction for signal attenuation, correction for vertical variation of precipitation, correction for fast-moving showers and use of uncertainty information in merging data from multiple radars.

Data set name: nl_rdr_data_rtcor_5m_tar

Data access: https://dataplatform.knmi.nl/dataset/access/nl-rdr-data-rtcor-5m-tar-1-0

API access: https://api.dataplatform.knmi.nl/open-data/v1/datasets/nl_rdr_data_rtcor_5m/versions/1.0/files

Ensure you have an updated API key, an anonymous operational / temporary key is available from: https://developer.dataplatform.knmi.nl/get-started#obtain-an-api-key

Review Buienradar archive: https://www.buienradar.nl/nederland/neerslag/buienradar-terugkijken/archief/202307171330 (local time)

Installation instructions for ffmpeg and ffprobe (if not available): https://json2video.com/how-to/ffmpeg-course/install-ffmpeg-linux.html (e.g. for 64-bit architecture based on Intel or AMD)

In [ ]:
#load required required libraries
from ctypes import *
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLdispatch.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGLX.so.0.0.0')
lib1 = cdll.LoadLibrary(r'/home/jovyan/.local/lib/libGL.so.1.7.0')

lib1 = cdll.LoadLibrary('/opt/conda/lib/libpython3.11.so.1.0')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Gui.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Sql.so.5')
lib1 = cdll.LoadLibrary('/opt/conda/envs/openeo/lib/libQt5Concurrent.so.5')

#install h5py to read the h5 format data
!pip install h5py

In [ ]:
#load libraries
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
from datetime import datetime, timedelta
import ilwis
import h5py
import numpy as np
import logging
import sys
from datetime import datetime
from pathlib import Path
import requests
import os
import glob
import warnings

#### Checking if ILWISPy is successfully loaded

In [ ]:
ilwis.version()

#### Creating a folder within the notebook directory to store the data, if not existing it will be created

In [ ]:
folder = 'radar_gauge_cor'
os.chdir(".")
print("current dir is: %s" % (os.getcwd()))

if os.path.isdir(folder):
    print("Folder exists")
else:
    print("Folder doesn't exists")
    os.mkdir(folder)

#### Assigning the folder as your (ILWISPy) working directory

In [ ]:
work_dir = os.getcwd() + '/' + folder 
print(work_dir)
ilwis.setWorkingCatalog(work_dir)

#### Define the starting time and the number of intervals to download the gauge corrected radar data.
Note time stamp required is UTC time and without registration you can download a maximum of 50 files

In [ ]:
#define start time (yyyymmddhhmm), note temporal interval is 5 minutes
#maximum number of files that can be downloaded in a single anonymous request = 50
#UTC to local time: + 2 hours during summer / + 1 hour during winter time
# 202307171130 UTC is 202307171330 Netherlands (summer)time
UTC_time = '202307171130' 
number_of_files = '36' # 3 hours

#### Creating a download instance
Based on the 'UTC_time' and the 'number_of_files' specified above the data (nl_rdr_data_rtcor_5m) will be retrieved from the 'api.dataplatform.knmi.nl/open-data'

In [ ]:
logging.basicConfig()
logger = logging.getLogger(__name__)
logger.setLevel("INFO")

api_url = "https://api.dataplatform.knmi.nl/open-data"
api_version = "v1"

# source = https://api.dataplatform.knmi.nl/open-data/v1/datasets/nl_rdr_data_rtcor_5m/versions/1.0/files
# https://api.dataplatform.knmi.nl/open-data/v1/datasets/nl_rdr_data_rfcor_5m/versions/1.0/files

def main():
# Parameters
    api_key = "eyJvcmciOiI1ZTU1NGUxOTI3NGE5NjAwMDEyYTNlYjEiLCJpZCI6ImE1OGI5NGZmMDY5NDRhZDNhZjFkMDBmNDBmNTQyNjBkIiwiaCI6Im11cm11cjEyOCJ9"
    dataset_name = "nl_rdr_data_rtcor_5m"
    dataset_version = "1.0"
    max_keys = number_of_files 

#maximum number of files that can be downloaded in a single anonymous request = 50
#note total number is 288 files / day - repeat this code field untill all files have been retrieved
#by modifying the hour-minute timestamp in "UTC_time"

# Use list files request to request 'number of files' files after 'start_after_filename_prefix' time stamp.
    start_after_filename_prefix = f"RAD_NL25_RAC_RT_"+UTC_time
    list_files_response = requests.get(
        f"{api_url}/{api_version}/datasets/{dataset_name}/versions/{dataset_version}/files",
        headers={"Authorization": api_key},
        params={"maxKeys": max_keys, "startAfterFilename": start_after_filename_prefix},
    )
    list_files = list_files_response.json()

    logger.info(f"List files response:\n{list_files}")
    dataset_files = list_files.get("files")

# Retrieve files in the list files response
    dataset_files = [f.get("filename") for f in dataset_files]
    print(dataset_files)
    for filename in dataset_files:
        logger.info(f"Retrieve file with name: {filename}")
        endpoint = f"{api_url}/{api_version}/datasets/{dataset_name}/versions/{dataset_version}/files/{filename}/url"
        get_file_response = requests.get(endpoint, headers={"Authorization": api_key})
        if get_file_response.status_code != 200:
            logger.error("Unable to retrieve download url for file")
            logger.error(get_file_response.text)
            sys.exit(1)    
        
        download_url = get_file_response.json().get("temporaryDownloadUrl")
        dataset_file_response = requests.get(download_url)
        if dataset_file_response.status_code != 200:
            logger.error("Unable to download file using download URL")
            logger.error(dataset_file_response.text)
            sys.exit(1)

# Write dataset file to disk
        p = Path(work_dir+'/'+filename)
        p.write_bytes(dataset_file_response.content)
        logger.info(f"Successfully downloaded dataset file to {p}")


if __name__ == "__main__":
    main()


#### Create a list of the downloaded files
Creates an empty list ('res'), iterates the folder and appends all downloaded filenames to the list with the extension '.h5'

In [ ]:
# list to store files
res = []
# Iterate directory
for file in os.listdir(work_dir):
    # check only h5 files
    if file.endswith('.h5'):
        res.append(file)
print(res)

#### Create a definition ('def')
To define a function, 'def' is placed before the function name 'openh5' provided to create a user-defined function that allows to read an instance of the 'h5' data that was downloaded

In [ ]:
def openh5(filename):
    try:
        f = h5py.File(filename, 'r')
        f.close
        return f
    except:
        print('File {:s} cannot be opened'.format(filename))
        return []

#### Read - import all h5 file instances
Within a loop the data files assigned to 'res' are imported using the user defined function created. Note the 'h5' structure as the data of our interest in stored in the h5-layer 'image1/image_data'. Each new dataset is appended to the already imported data.
From the file also the image size (columns, rows) is obtained.

In [ ]:
image_size = None
band_data = []

for f in (res):
    print ('now processed = ',f)
    f = openh5(work_dir + '/' + f)
    image = f['image1']['image_data'][()]
    
    band_data.append(image)
    if image_size is None:
        # image_size contains the number of pixels of the images
        image_size = [f['geographic'].attrs['geo_number_columns'][0], f['geographic'].attrs['geo_number_rows'][0]]

print(image_size)

#### Retrieve the resulting array dimensions (col, row and number of layers)

In [ ]:
print(image_size[0], image_size[1])
print(len(res))

#### Using FFMPEG for time series data visualization
FFMPEG (Fast Forward Moving Picture Experts Group) is a free and open source software project that offers many tools for video and audio processing. It's designed to run on a command line interface and has utilities to visualize, manipulate and handle video files.
In the first code field of this notebook the files 'ffmpeg' and 'ffprobe' are copied into a folder in the path of the Python / Jupyter Notebook environment, so it is available for the 'user'

In [ ]:
#create animation of raw imported data
#note that background data is still included
imageList = band_data
fig = plt.figure(figsize=(8, 8))
ims = []

for i in range(len(imageList)):
    im = plt.imshow(imageList[i], vmin='0', vmax='155', cmap='jet', animated=True)
    ims.append([im])
    
ani = animation.ArtistAnimation(fig, ims, interval=400, blit=True, repeat=True)

plt.xticks(color='w')
plt.yticks(color='w')
plt.colorbar(shrink=0.65)
plt.grid(True, alpha = 0.5)
plt.title("Rainfall animation raw data, StereoGraphic projection");
plt.close()

# Show the animation inline (below)
HTML(ani.to_html5_video())

The animation created inline above can also be written to disk, uncomment the line in the code field below to save animation as a mp4 video. 

In [ ]:
#ani.save(work_dir+'/ani_raw.mp4', fps=2)

#### Some ILWISPy processing
First we create a georeference (using a Proj4 format - a library for performing conversions between cartographic projections) and then assign this to an empty raster coverage and subsequently fill it with the data imported before and review the projection and dimensions (x, y, z) of the new ilwis map list (data stack) created. 

In [ ]:
#data is in a StereoGrapic projection, False Easting=0 degree, False Northing=90 degree, Central Meridian=0 degree, Central Parallel=60 degree, Ellipsoid=WGS 84, Scale Factor=1.0 
#from meta data information provided: +proj=stere +lat_0=90 +lon_0=0 +lat_ts=60 +a=6378.14 +b=6356.75 +x_0=0 y_0=0 - note 'a' and 'b' are given in km
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=stere +lat_0=60 +lon_0=0 +lat_ts=60 +a=6378137 +b=6356750 +x_0=0 +y_0=90 +datum=WGS84 +units=m, envelope=0 -448497.662 686614.850 -1196791.122, gridsize=700 765,cornerofcorners=yes')

In [ ]:
#create empty ilwis raster 
pcpAll = ilwis.RasterCoverage()
defNumr = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(0, 1000, 0))
pcpAll.setDataDef(defNumr)
pcpAll.setSize(ilwis.Size(int(image_size[0]), int(image_size[1]), len(res)))
pcpAll.setGeoReference(grf)

In [ ]:
#read all the data from the initial numpy array as an ilwis map list (pixel by pixel) as a 1 dimensional array - based on (flatten) reduced dimensions and resize it into a 3D array
pcpAll.array2raster(np.array(band_data).flatten())
print(pcpAll.size())

#### Check the ILWISPy mapList created, like it's size, bounding coordinates and coordinate system

In [ ]:
print(pcpAll.size())
print(pcpAll.envelope())
pcpAllcoordSys = pcpAll.coordinateSystem()
print(pcpAllcoordSys.toWKT())
print(pcpAllcoordSys.toProj4())

In [ ]:
#uncomment line below if you want to store results of the raw data as an ILWIS maplist
#pcpAll.store('pcp_raw.mpl')

#### Perform data scaling
From the meta data the scaling coefficient obtained ('0.01') which is used to fransform the data from integer format into a float, unit is accumulation (per time step) in mm, here time step is 5 minutes. Note ILWISPy performs calculation on all layers in the 3D stack.

In [ ]:
#apply calibration formulas = GEO = 0.010000*PV+0.000000
pcp_acc5m = ilwis.do('mapcalc', '0.01 * @1', pcpAll)

In [ ]:
#uncomment line below if you want to store results of the processed data as an ILWIS maplist
#pcp_acc5m.store('pcp_acc5m.mpl')

#### Calculate the sum of the precipitation over the time period 
An aggregation factor 'sum' is used, also a calculation is performed to set values higher or equal to 655 as background, by assigning these as 'no-data', ILWISPy uses the '?' syntax to represent 'no-data'

In [ ]:
#aggregation to get total over time period
R_sum = ilwis.do('aggregaterasterstatistics', pcp_acc5m, 'sum') # add all 5 minutes accumumulated timesteps
R_sum_fin = ilwis.do('mapcalc', 'iff(@1<655, @1, ?)', R_sum) # remove background

#### Write / store the resulting map to disk

In [ ]:
R_sum_fin.store('pcp_accum_gauge_cor_stgr.mpr')

#### Temporary issue
To display the map in ILWIS386, the coordinate system created 'pcp_accum_gauge_cor_stgr.csy' has to be adapted. The code field below changes 'Projection=?' into 'Projection=StereoGraphic'. Now you can display the map without an error message.

In [ ]:
#input file
fin = open(work_dir+"/pcp_accum_gauge_cor_stgr.csy", "rt")
#output file to write the result to
fout = open(work_dir+"/temp.csy", "wt")
#for each line in the input file
for line in fin:
    #read replace the string and write to output file
    fout.write(line.replace('Projection=?', 'Projection=StereoGraphic'))
#close input and output files
fin.close()
fout.close()

#remove file
if os.path.exists(work_dir+"/pcp_accum_gauge_cor_stgr.csy"):
  os.remove(work_dir+"/pcp_accum_gauge_cor_stgr.csy")
else:
  print("The file does not exist")


old_name = work_dir+"/temp.csy"
new_name = work_dir+"/pcp_accum_gauge_cor_stgr.csy"
# Renaming the file
os.rename(old_name, new_name)

#### Resample the map to UTM - zone 32N
Here as example the data is changed from StereoGraphic into a UTM projection, zone 32N, note the EPSG code, the last 2 digits represent the zone number. First a new georeference is created, covering only the area of the Netherlands.

In [ ]:
#transform from stereographic to UTM projection, here zone 32 -'EPSG:32632' 
#create target georeference
grf_utm = ilwis.GeoReference('code=georef:type=corners, csy=epsg:32632, envelope= 84512.281 5591939.637 401512.281 5954939.637, gridsize=317 363, cornerofcorners=yes')

In [ ]:
print(grf_utm.coordinateSystem())

#### Conduct the resampling, using a nearest neighbour resamping method

In [ ]:
R_sum_res = ilwis.do('resample', R_sum_fin, grf_utm, 'nearestneighbour')

In [ ]:
print(R_sum_res.size())

#### Save your results on disk
First method writes an ILWIS output raster map the second method creates a GeoTiff, e.g. so it can be used in QGIS

In [ ]:
R_sum_res.store('gauge_cor_radar_sum_utm.mpr')
R_sum_res.store('gauge_cor_radar_sum_utm.tif', 'GTiff', 'gdal')

#### Animation result UTM resampled data
To prepare an animation we use the UTM resampled submap - time series. First we remove the background, then use is made of the ILWISPy pixel iterator to write the output time series to a numpy array. This array is saved on disk as we need to load it at a later stage. We subsequently create a masked array, eliminating the areas without precipitation before creating another animation instance. 

In [ ]:
#now resample the whole time series
R_ts_res = ilwis.do('resample', pcp_acc5m, grf_utm, 'nearestneighbour')

In [ ]:
print(R_ts_res.size())

In [ ]:
#remove background
R_ts5 = ilwis.do('mapcalc', 'iff(@1<655, @1, ?)', R_ts_res) 

In [ ]:
R_ts5.store('pcp_ts5.tif', 'GTiff', 'gdal')

In [ ]:
#transform to numpy array
R_ts5_2np = np.fromiter(iter(R_ts5), np.float64, R_ts5.size().linearSize()) 
R_ts5_2np = R_ts5_2np.reshape((R_ts5.size().zsize, R_ts5.size().ysize, R_ts5.size().xsize))

In [ ]:
#save numpy array on disk
np.save(work_dir+'/np_save', R_ts5_2np)

In [ ]:
#create masked array
R_ts5_2np = np.ma.masked_where(R_ts5_2np < 0.001, R_ts5_2np) #set background to white for animation

In [ ]:
#create animation
imageList = R_ts5_2np

fig = plt.figure(figsize=(8, 8))
ims = []

for i in range(len(imageList)):
    im = plt.imshow(imageList[i], vmin='0', vmax='4', cmap='jet', animated=True)
    ims.append([im])
    
ani = animation.ArtistAnimation(fig, ims, interval=400, blit=True, repeat=True)

plt.xticks(color='w')
plt.yticks(color='w')
plt.colorbar(shrink=0.65)
plt.grid(True, alpha = 0.5)
plt.title("Rainfall animation processed data over the Netherlands, UTM projection");
plt.close()

# Uncomment line below to save animation as video 
#ani.save(work_dir+'/ani.mp4', fps=2)

# Show the animation inline (below)
HTML(ani.to_html5_video())

#### Precipitation time series values for certain location
First we specify a location (using line and column position) and extract the time series values, then we create the time annotation to be used on the x-axis of the plot. Finally the plot is created

In [ ]:
l = 158
c = 192

z = (R_ts5.size().zsize)
print(z)

PCP_values = []
for n in range(0,(z)):
    point_value = (R_ts5.pix2value(ilwis.Pixel(c,l,n)))
    PCP_values.append(point_value)

print('Values extracted for selected location:', PCP_values)

In [ ]:
# initializing time range for X-Axis
plot_date = datetime.strptime("13:30", "%H:%M")

z = (R_ts5.size().zsize)

current_time = plot_date
end_time = plot_date + timedelta(hours=3) 
interval = timedelta(minutes=5)

date_ts = []
while current_time < end_time:
    time_ts = (current_time.strftime("%H:%M"))
    current_time += interval
    date_ts.append(time_ts)

print(date_ts)

In [ ]:
fig = plt.figure(figsize =(8, 5))
plt.plot(date_ts, PCP_values, label='Rainfall')
plt.ylim(0, 2)#set value range for y-axis
frequency = 3
plt.xticks(date_ts[::frequency])#plot only 15 minutes time step on x-axis
plt.xlabel('Time period selected')
plt.ylabel('Accumulated rainfall (mm/5-min)')
plt.title('Rainfall extracted for a specific location')
plt.legend();

#### Display the resulting accumulated radar - gauge corrected precipitation map with additional background references 
Within Python use is made of Cartopy to e.g. add vector information to a map visualization. Currently ILWISPy and Cartopy use different versions of GDAL, therefore they are not compatible and we need to start a new instance of the kernel, load the required libraries - now without ILWISPy

#### Shutdown the current notebook instance
We shutdown the Jupyter Notebook instance, press 'OK' to start a new instance

In [ ]:
import IPython
IPython.Application.instance().kernel.do_shutdown(True) #automatically restarts kernel

#### Install Cartopy
Likely Cartopy is not available within your Python environment so we need to install it, note the exclamation mark ( ! ) invokes a Python instance

In [ ]:
#install Cartopy
!pip install cartopy
!pip install pykdtree

#### Load required libraries - sitepackages

In [ ]:
#import required libraries
from cartopy import crs as ccrs, feature as cfeature
import cartopy.io.img_tiles as cimgt
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML
from datetime import datetime, timedelta
import numpy as np
import os
import warnings

#### Set folder and assig this as your active directory

In [ ]:
folder = 'radar_gauge_cor'
os.chdir(".")
print("current dir is: %s" % (os.getcwd()))

if os.path.isdir(folder):
    print("Folder exists")
else:
    print("Folder doesn't exists")
    os.mkdir(folder)

In [ ]:
work_dir = os.getcwd() + '/' + folder 
print(work_dir)

#### Load previously saved numpy array

In [ ]:
#load numpy array
R_all_res = np.load(work_dir+'/np_save.npy')

#### Check the shape of your array
Note we are working with time series, so data array is 3D!

In [ ]:
R_all_res.shape

#### Create a masked array
Areas having no rainfall will appear white

In [ ]:
R_ts5_2np = np.ma.masked_where(R_all_res < 0.001, R_all_res) #set background to white for animation

#### Display first layer of time series
Using Cartopy we set the projection to UTM, zone 32, with the plot extent of our map. Then the coastline and country borders are added as well as the first layer of our array 'R_ts5_2np[0]' and this is plotted using 'imshow'

In [ ]:
warnings.filterwarnings('ignore')

fig = plt.figure(figsize=(12, 9))
subplot_extent = [84512, 401512, 5591939, 5954939]

request = cimgt.OSM()
#request = cimgt.QuadtreeTiles()
projection = ccrs.UTM(32)

ax = fig.add_subplot(projection=projection)
ax.set_extent(subplot_extent, projection)


ax.coastlines(linewidth=0.5, color='blue')
ax.add_feature(cfeature.BORDERS, linewidth=0.5, color='red')
plt.imshow(R_ts5_2np[0], extent=subplot_extent,  interpolation = 'None', vmin='0', vmax='4', cmap='jet', alpha=1) #first rainfall event
ax.add_image(request, 8, alpha=0.3)
ax = plt.subplot(1, 1, 1, projection=ccrs.UTM(32))

plt.colorbar(shrink=0.65)
ax.set_title("Rainfall timestep-1, UTM projection");


#### Final animation
With the projection and additional layers displayed correctly we can now create the animation of the rainfall time series, we also include the time stamp for every time step. Use is made of 'datetime' to define a list of time steps which can be included in the annotation when the animation is created

In [ ]:
start_time = datetime(2023, 7, 17, 13, 30) # Replace this with your desired start time
end_time = start_time + timedelta(hours=3)  # Replace this with your desired end time

current_time = start_time
interval = timedelta(minutes=5)

ts = []
while current_time < end_time:
    time_ani = (current_time.strftime("%H:%M"))
    current_time += interval
    ts.append(time_ani)
print(ts)

In [ ]:
warnings.filterwarnings('ignore')

imageList = R_ts5_2np

fig = plt.figure(figsize=(9, 9))
subplot_extent = [84512.281, 401512.281, 5591939.637, 5954939.637]


request = cimgt.OSM()
#request = cimgt.QuadtreeTiles()
projection = ccrs.UTM(32)


ax = plt.axes(projection=projection)
ax.set_extent(subplot_extent, projection)


ax.coastlines(color='blue', linewidth=0.5, alpha=0.3)
ax.add_feature(cfeature.BORDERS, linewidth=0.5, color='red', alpha=0.3)
ax.add_image(request, 8, alpha=0.3)

ims = []
for i in range(len(imageList)):
    im = plt.imshow(imageList[i], extent=subplot_extent, interpolation = 'None', vmin='0', vmax='4', cmap='jet', animated=True, alpha=1)
    #ann = ax.annotate(f"Time step {i:.0f}.", (1.0, 1.01), xycoords="axes fraction", ha="right")
    ann = ax.annotate (f'20230717 - {ts[i]}',(1.0, 1.01), xycoords="axes fraction", ha="right")
    ims.append([im, ann])
    
ani_fin = animation.ArtistAnimation(fig, ims, interval=400, blit=True, repeat=True)


ax = plt.subplot(1, 1, 1, projection=projection)
ax.set_title("Rainfall animation 3 hours, UTM projection", loc='left');
clb = plt.colorbar(shrink=0.65)
clb.ax.set_title('Accum-PCP',x=1.07) 
clb.ax.set_ylabel('(mm/timestep)', labelpad=20, rotation=90) 
plt.close()

# Show the animation inline (below)
HTML(ani_fin.to_html5_video())

In [ ]:
# Uncomment line below to save animation as video 
#ani_fin.save(work_dir+'/ani_fin.mp4', fps=2)

#uncomment line below to remove numpy array stored on disk
#os.remove(work_dir+"/np_save.npy")